In [1]:
# This ensures Plotly output works in multiple places:
# plotly_mimetype: VS Code notebook UI
# notebook: "Jupyter: Export to HTML" command in VS Code
# See https://plotly.com/python/renderers/#multiple-renderers
import plotly.io as pio
pio.renderers.default = "plotly_mimetype+notebook"

In [2]:
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)  

In [3]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objs as go
from plotly.subplots import make_subplots
from sklearn.cluster import KMeans, AgglomerativeClustering
import random
import time
from kneed import KneeLocator
from geopy.distance import geodesic
from scipy.stats import pearsonr


In [4]:
from sklearn.metrics import silhouette_score

# Clustering of pokemon spawns

### What's in this notebook:
#### EDA
- plot different pokemon spawns on map, visually analyse patterns

#### K-means clustering
- cluster spawns by latitude and longitude
(to-do: use different methods to find optimal number of clusters)
- clutser pokemons based on occurences in clusters


*Potential analysis: Travelling Salesman Problem*


### About the data

The dataset contains Pokemon Go spawns in the San Francisco Bay Area over a three-day period from 26th to 28th Jul 2016. It jas the following fields: 
* num: number of spawn instances
* name: name of the pokemon
* lat & lng: latitude and longitude of the spawn
* encounter_ms: unix timestamp of the encounter
* disappear_ms: unix timestamp of when it disappears

Data source: Kaggle https://www.kaggle.com/datasets/kveykva/sf-bay-area-pokemon-go-spawns

## Data cleaning

In [5]:
df_complete = pd.read_csv('data/pokemon-spawns.csv')

### Sense check latitudes and longitudes

In [6]:
print('Latitude: \n', df_complete['lat'].describe(), '\n')
print('Longitude: \n', df_complete['lng'].describe(), '\n')

Latitude: 
 count    314105.000000
mean         37.291383
std           1.918667
min          32.188748
25%          37.322103
50%          37.615938
75%          37.788990
max          43.164284
Name: lat, dtype: float64 

Longitude: 
 count    314105.000000
mean        -95.059814
std          73.256881
min        -122.611804
25%        -122.337013
50%        -122.106334
75%        -118.260931
max         139.840451
Name: lng, dtype: float64 



### Detect outliers
It appears that some spawns are outside of the SF Bay Area. To identify outliers, I tried two methods: 
1. z-scores < 3: z-score measures the number of standard deviations a data point is away from the mean. Outliers are any data points with z-score > 3. This is based on the statistical rule that for a normal distribution, 99.7% of all observed data would fall within 3 standard deviations of the mean. 
<br>
2. inter-quartile range (IQR): the inter-quartile range refers to the difference between the 3rd and 1st quartile. This method considers data points 1.5 IQR above 3rd quartile or 1.5 IQR below 1st quartile to be the outlier, which is mathematically comparable to the z-score < 3 method*. 

    <i>\* By definition, 50% of data lies between 1st and 3rd quartile. With a normal distribution, ~50% of data lies between +/- 0.7 standard deviations. This means that the IQR is roughly comparable to to 0.7 x 2 = 1.4 standard deviations, and the lower/upper bounds are defined such that they are around 3 standard deviations from the mean (0.7 + 1.5 x 1.4 = 2.8).</i> 

**1. Z-Score**

In [7]:
from scipy import stats
df_complete['lat_zscore'] = np.abs(stats.zscore(df_complete['lat']))
df_complete['lng_zscore'] = np.abs(stats.zscore(df_complete['lng']))

In [8]:
print('Latitude (z-score < 3): \n', df_complete[df_complete['lat_zscore']<3]['lat'].describe(), '\n')
print('Longitude (z-score < 3): \n', df_complete[df_complete['lng_zscore']<3]['lng'].describe(), '\n')

Latitude (z-score < 3): 
 count    306444.000000
mean         37.145566
std           1.703384
min          32.188748
25%          37.315651
50%          37.598394
75%          37.779847
max          40.818783
Name: lat, dtype: float64 

Longitude (z-score < 3): 
 count    287022.000000
mean       -117.214987
std          13.420221
min        -122.611804
25%        -122.371368
50%        -122.159748
75%        -121.901929
max         -73.357929
Name: lng, dtype: float64 



**2. Inter-Quartile Range**

In [9]:
q1 = np.percentile(df_complete['lat'], 25, method='midpoint')
q3 = np.percentile(df_complete['lat'], 75, method='midpoint')
iqr = q3 - q1
lat_lower_bound = q1-1.5*iqr
lat_upper_bound = q3+1.5*iqr

q1 = np.percentile(df_complete['lng'], 25, method='midpoint')
q3 = np.percentile(df_complete['lng'], 75, method='midpoint')
iqr = q3 - q1

lng_lower_bound = q1-1.5*iqr
lng_upper_bound = q3+1.5*iqr

In [10]:
print('Latitude (IQR rule): \n', df_complete[(df_complete['lat']>lat_lower_bound)
                                               &(df_complete['lat']<lat_upper_bound)]['lat'].describe(), '\n')
print('Latitude (IQR rule): \n', df_complete[(df_complete['lng']>lng_lower_bound)
                                               &(df_complete['lng']<lng_upper_bound)]['lng'].describe(), '\n')


Latitude (IQR rule): 
 count    222939.000000
mean         37.635558
std           0.196614
min          36.621860
25%          37.477212
50%          37.682257
75%          37.784168
max          37.998836
Name: lat, dtype: float64 

Latitude (IQR rule): 
 count    248309.000000
mean       -121.889323
std           1.114851
min        -122.611804
25%        -122.403057
50%        -122.210387
75%        -121.996139
max        -118.164244
Name: lng, dtype: float64 



Both the z-score and IQR methods resulted in a data set that contains points significantly outside the SF Bay Area. So in the end, I simply took the border coordinates of the SF Bay Area since that was the author's intended scope of the data set. 

In [11]:
df = df_complete[(df_complete['lng']>=-122.6445)
                &(df_complete['lng']<-121.5871)
                &(df_complete['lat']>=37.1897)
                &(df_complete['lat']<38.2033)
                ]

df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 221979 entries, 0 to 314104
Data columns (total 10 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   s2_id         221979 non-null  int64  
 1   s2_token      221979 non-null  object 
 2   num           221979 non-null  int64  
 3   name          221979 non-null  object 
 4   lat           221979 non-null  float64
 5   lng           221979 non-null  float64
 6   encounter_ms  221979 non-null  int64  
 7   disppear_ms   221979 non-null  int64  
 8   lat_zscore    221979 non-null  float64
 9   lng_zscore    221979 non-null  float64
dtypes: float64(4), int64(4), object(2)
memory usage: 18.6+ MB


Then i converted pokemon name field to dummy variables (for analysing patterns later)

In [12]:
pokemon_dummies = pd.get_dummies(df['name'], prefix='pkm')
df = pd.concat([df, pokemon_dummies], axis=1).dropna()

In [13]:
df['spawn_latlng'] = list(zip(df['lat'], df['lng']))

## Exploratory Data Analysis

### Scatter map for all pokemon species
First I will plot the data on a map to check if there are any visible clusters. It looks like there are many small clusters and that are arbitrarily shaped (e.g. the clusters along the waterfront appears to be elongated whereas the inland clusters are more spherical. 

In [14]:
# the mapbox access token can be created for free by registering on mapbox. the token allows access to more base map options
with open('../mapboxtoken.txt', 'r') as file:
    mapboxtoken = file.read()

In [15]:
# set the GPS coordinates for map centre
map_centre = {'lat':37.6965, 'lon':-122.1158}

In [16]:
# the data set has >300k data points, which makes plotting very slow
# therefore I selected a random sample of 10% of the points to plot on the map
random.seed(42)
plot_sample_indices = random.sample(df.reset_index().index.tolist(), int(len(df)/10))
df_plot_sample = df.iloc[plot_sample_indices].copy(deep=True)

In [17]:
fig = go.Figure()
fig.add_trace(go.Scattermapbox( lat=df_plot_sample['lat'],  
                                lon=df_plot_sample['lng'], 
                                mode='markers',
                                marker=go.scattermapbox.Marker(size=df_plot_sample['num']/20, 
                                                              opacity=.7)
                              ))
# update mapbox style and layout
fig.update_mapboxes(
    domain=dict(column=2),
    style='mapbox://styles/mapbox/light-v10',
    zoom=9.5,
    center={'lat':37.6965, 'lon':-122.30}
)

fig.update_layout(height=600, margin_t=50, mapbox_accesstoken=mapboxtoken, showlegend=False)

fig.show()

### Scatter map by species
Besides clustering the spawns, I am also interested to see whether certain pokemon species are more concentrated in some areas but not others. So I created scatter maps for a few relatively common species. 

*I used a different data visualisation package called Folium (I used Plotly for the previous chart) purely for aesthetic reason because Folium allows me to replace circular markers with pokemon icons.*

As the maps below show, the different pokemon species do have different geographic distributions. Pikachus are more concentrated in the south (Palo Alto, Mountain View), whereas Squirtle and Bulbasaur are more frequently found in the north of San Mateo. Jigglypuff is most evenly distributed among the four species selected. 

In [18]:
top_50_pokemons = df['name'].str.lower().value_counts().head(50).index.tolist()

In [19]:
df_plot_sample_pkm_dict = {}
for pkm in df['name'].str.lower().unique():#'pikachu', 'squirtle', 'bulbasaur', 'jigglypuff', 'voltorb', 'krabby', 'staryu']:
    df_plot_sample_pkm_dict[pkm]= df_plot_sample[df_plot_sample['name'].str.lower()==pkm] 

In [20]:
import folium.plugins

m = folium.plugins.DualMap(location=[37.6965,-122.1158], tiles="Cartodb Positron", zoom_start=9)

for i in range(len(df_plot_sample_pkm_dict['pikachu'])-1):#stations['features']:
    lon, lat = df_plot_sample_pkm_dict['pikachu'].iloc[i]['lng'], df_plot_sample_pkm_dict['pikachu'].iloc[i]['lat']
    icon_path = '../static/img/pkm-pikachu.ico'
    icon = folium.features.CustomIcon(icon_path,
                                      icon_size=(20, 20))
    marker = folium.map.Marker([lat, lon], icon=icon,
                              )
    m.m1.add_child(marker)

for i in range(len(df_plot_sample_pkm_dict['squirtle'])-1):#stations['features']:
    lon, lat = df_plot_sample_pkm_dict['squirtle'].iloc[i]['lng'], df_plot_sample_pkm_dict['squirtle'].iloc[i]['lat']
    icon_path = '../static/img/pkm-squirtle.ico'
    icon = folium.features.CustomIcon(icon_path,
                                      icon_size=(20, 20))
    
    marker = folium.map.Marker([lat, lon], icon=icon,
                              )
    m.m2.add_child(marker)
    

In [21]:
n = folium.plugins.DualMap(location=[37.6965,-122.1158], tiles="Cartodb Positron", zoom_start=9)

for i in range(len(df_plot_sample_pkm_dict['bulbasaur'])-1):#stations['features']:
    lon, lat = df_plot_sample_pkm_dict['bulbasaur'].iloc[i]['lng'], df_plot_sample_pkm_dict['bulbasaur'].iloc[i]['lat']
    icon_path = '../static/img/pkm-bulbasaur.ico'
    icon = folium.features.CustomIcon(icon_path,
                                      icon_size=(20, 20))
    marker = folium.map.Marker([lat, lon], icon=icon,
                              )
    n.m1.add_child(marker)

for i in range(len(df_plot_sample_pkm_dict['jigglypuff'])-1):#stations['features']:
    lon, lat = df_plot_sample_pkm_dict['jigglypuff'].iloc[i]['lng'], df_plot_sample_pkm_dict['jigglypuff'].iloc[i]['lat']
    icon_path = '../static/img/pkm-jigglypuff.ico'
    icon = folium.features.CustomIcon(icon_path,
                                      icon_size=(20, 20))
    
    marker = folium.map.Marker([lat, lon], icon=icon,
                              )
    n.m2.add_child(marker)

In [22]:
print('L: Pikachu, R:Squirtle')
m

L: Pikachu, R:Squirtle


In [23]:
print('L: Bulbasaur, R: Jigglypuff')
n

L: Bulbasaur, R: Jigglypuff


## Clustering
In this section I will experiment with two clustering methods, k-means and DBSCAN to group together spawn locations that are close to each other. Then I will explore whether there are pokemon species that occur near each other by counting the number of spawns for each species in each cluster, and looking at the pairwise correlation between species.   

### K-Means Clustering

K-Means clustering is an unsupervised learning algorithm that partitions the data into K non-overlapping subgroups. It takes an iterative approach to find the optimal clustering that minimizes the within-cluster sum of squares (sum of squared distances between each data point and the centroid of its assigned cluster.

Step 1 - select K random points as initial centroids \
Step 2 - calculate the Euclidean distance between each point and each centroid, and assign each point to its nearest centroid \
Step 3 - update centroids by calculating the mid point of each cluster \
Step 4 - repeat steps 2 and 3 until no changes

To determine the optimal number of clusters, I will explore two methods: 
1. Elbow method
2. Silhouette score

#### Elbow method
The Elbow method is a graphical technique which involves plotting the within-cluster sum of squares (WCSS) against the number of clusters. The WCSS measures the sum of squared distances (geodesic distance is used instead of Euclidean because we are clustering GPS coordinates). The idea is to choose the number of clusters at which the decrease in WCSS slows (diminishing returns to additional clusters set in). 

The graph suggests that 30 is the optimal number of clusters as that is the point where the slope starts to decrease slower. 

In [24]:
df_lat_lng = np.array(df[['lat', 'lng']]).tolist()

In [25]:
# within-cluster sum of squares / WCSS (sum of the distances between each point and the centroid of the cluster it belongs to)
start = time.time()
wcss = {}
kmeans_dict = {}
df_centroids_dict = {}


for i in np.arange(10, 101, 10):
# for i in np.arange(5, 101, 10):
# for i in [2]:
    if i not in wcss.keys():
        kmeans = KMeans(n_clusters=i, random_state=42, n_init="auto").fit(df_lat_lng)
        kmeans_dict[i] = kmeans

        df_centroids = pd.DataFrame(kmeans.cluster_centers_, columns=['lat', 'lng']).reset_index(names='cluster_id')
        df_centroids['size'] = pd.Series(kmeans.labels_).value_counts()
        df_centroids_dict[i] = df_centroids

        df['cluster_id_'+str(i)] = kmeans.labels_
        df['centroid_lat_'+str(i)] = df['cluster_id_'+str(i)].map(df_centroids.set_index('cluster_id')['lat'])
        df['centroid_lng_'+str(i)] = df['cluster_id_'+str(i)].map(df_centroids.set_index('cluster_id')['lng'])
        df['centroid_latlng_'+str(i)] = list(zip(df['centroid_lat_'+str(i)], df['centroid_lng_'+str(i)]))
        df['geodesic_dist_'+str(i)] = df.apply(lambda x: geodesic(x['spawn_latlng'], 
                                                                           x['centroid_latlng_'+str(i)]).kilometers, axis=1)

        wcss[i] = df['geodesic_dist_'+str(i)].apply(lambda x: x**2).sum()

        print(i, 'clusters completed')
print('{:,.0f}s'.format(time.time() - start))

10 clusters completed
20 clusters completed
30 clusters completed
40 clusters completed
50 clusters completed
60 clusters completed
70 clusters completed
80 clusters completed
90 clusters completed
100 clusters completed
872s


In [26]:
df_ = pd.DataFrame(wcss, index=['wcss']).transpose().reset_index(names='clusters')
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_['clusters'], y=df_['wcss'], mode='lines+markers'))
fig.update_layout(plot_bgcolor='rgba(0, 0, 0, 0)',
                  title='Elbow method',
                  xaxis=dict(title='Number of clusters'),
                  yaxis=dict(title='total within sum of squares'),
                  height=400, width=600
                 )
fig.show()

The 'Kneedle' algorithm also finds 30 as the point where the curve starts to flatten. \
*Kneedle algorithm was publisehd by Satopää, Albrecht, Irwin, and Raghavan (2011) [https://raghavan.usc.edu/papers/kneedle-simplex11.pdf]

In [27]:
kn = KneeLocator(df_['clusters'], y=df_['wcss'], curve='convex', direction='decreasing')
print(kn.knee)

30


#### Silhouette score
The silhouette score is a measure of how similar an object is to its own cluster compared to other clusters. The method involves calculating for each data point:
1. intra-cluster distance (ICD) = the avgerage distance between the point and all other points in its cluster
2. nearest-cluster distance (NCD) = the average distance between the point and all points in the nearest neighbouring cluster
3. silhouette score = (NCD-ICD) / max(ICD, NDC)

The optimal number of clusters is the one that resulted in the highest average silouette score across all points. 

As shown below, the highest avearge silhouette score is 0.44, from splitting the data into ten clusters. This contradicts with the Elbow method which found 30 to be the optimal number of clusters. 

Since k-means clustering responds poorly to non-convex shaped (e..g elongated) clusters, I will attempt a density-based clustering method in the next part. 

In [28]:
geodesic_scores_dict = {}
for i in kmeans_dict.keys(): #np.arange(10, 101, 10):
    start = time.time()
    geodesic_score = silhouette_score(df_lat_lng, kmeans_dict[i].labels_, metric="haversine", sample_size=3000)
    geodesic_scores_dict[i] = geodesic_score

In [29]:
pd.DataFrame(geodesic_scores_dict, index=['silhouette_score_total']).transpose().reset_index(names='clusters').sort_values('clusters')

clusters  silhouette_score_total
0        10                0.455609
1        20                0.407667
2        30                0.372189
3        40                0.344534
4        50                0.347550
5        60                0.353839
6        70                0.358182
7        80                0.364611
8        90                0.350712
9       100                0.352709

In [30]:
colors = (px.colors.qualitative.Pastel1[:-1]
          +px.colors.qualitative.Set3
          +px.colors.qualitative.Set1
          +px.colors.qualitative.Set2
          +px.colors.qualitative.Antique
          +px.colors.qualitative.Bold
          +px.colors.qualitative.Prism
          +px.colors.qualitative.Pastel
          +px.colors.qualitative.Vivid
          +px.colors.qualitative.Safe
          +px.colors.qualitative.Plotly
          +px.colors.qualitative.D3
          +px.colors.qualitative.G10
          +px.colors.qualitative.Alphabet          
          +px.colors.qualitative.Pastel2
         # +['rgb(0,0,0)']
         )

In [31]:
fig = go.Figure()

sample_indices = random.sample(df.reset_index().index.tolist(), int(len(df)/10))
df_plot_sample_kmeans = df.iloc[sample_indices].copy(deep=True)[['cluster_id_30', 'lat', 'lng']]
df_plot_sample_kmeans['cluster_color'] = df_plot_sample_kmeans['cluster_id_30'].apply(lambda x: colors[x])

# for cl in sorted(df_sample['cluster_id_db'].unique(), reverse=True):
fig.add_trace(go.Scattermapbox( lat=df_plot_sample_kmeans['lat'],  
                                lon=df_plot_sample_kmeans['lng'], 
                                mode='markers',
                                marker=go.scattermapbox.Marker(size=10, 
                                                              opacity=1, 
                                                              color=df_plot_sample_kmeans['cluster_color'], 
                                                              #colorbar=dict(title='cluster')
                                                              )
                              ))
# update mapbox style and layout
fig.update_mapboxes(
    domain=dict(column=2),
    style='mapbox://styles/mapbox/light-v10',
    zoom=7.8,
    center=map_centre
)

fig.update_layout(title='k-means, k=30', height=600, margin_t=50, showlegend=False, mapbox_accesstoken=mapboxtoken
                 )

fig.show()

## DBSCAN

DBSCAN is another unsupervised algorithm that identifies distinctive clusters in the data. Unlike K-Means, which is based on the concept of centroids, DBSCAN views clusters as regions of high density. The algorithm takes two parameters - the minimum sample size (n) and epsilon (eps). DBSCAN separates the data set into core samples, non-core samples, and outliers. 

Core sample: a data point that has at least n other points within the distance of eps \
Non-core sample: a data point that is the neighbour of a core sample but not a core sample itself \
Outliers: a sample that is not a neighbour of any other core sample

The advantage of DBSCAN is that it does not assume clusters to be convex in shape and can handle clusters of varying sizes. The downside is that it is computationally expensive for large data sets, which is why I performed the clustering on a subset of the data. 

In [32]:
from sklearn.cluster import DBSCAN

In [33]:
random.seed(42)
sample_indices = random.sample(df.reset_index().index.tolist(), 10000)
df_sample = df.iloc[sample_indices].copy(deep=True)

In [34]:
df_sample_lat_lng =  np.array(df_sample[['lat', 'lng']]).tolist()

In [35]:
min_samples_to_test = [5, 8, 10, 15, 20]

df_db_cluster_size = pd.DataFrame(index=min_samples_to_test)
df_db_outliers = pd.DataFrame(index=min_samples_to_test)
df_db_size_std = pd.DataFrame(index=min_samples_to_test)
df_db_size_skew = pd.DataFrame(index=min_samples_to_test)
df_db_silhouette = pd.DataFrame(index=min_samples_to_test)

for eps in [.005, .006, .007, .008, .01]:
    df_db_cluster_size[eps] = [None]*5
    df_db_outliers[eps] = [None]*5
    df_db_size_std[eps] = [None]*5
    df_db_size_skew[eps] = [None]*5
    df_db_silhouette[eps] = [None]*5
    
    for min_samples in min_samples_to_test:
        db = DBSCAN(eps=eps, min_samples=min_samples, metric='haversine', n_jobs=-1).fit(df_sample_lat_lng)
        df_sample[(eps, min_samples)] = db.labels_
        
        df_db_cluster_size.loc[min_samples, eps] = len(np.unique(db.labels_))
        df_db_outliers.loc[min_samples, eps] = sum(db.labels_==-1)
        df_db_size_std.loc[min_samples, eps] = df_sample.iloc[db.core_sample_indices_][(eps, min_samples)].value_counts().std()
        df_db_size_skew.loc[min_samples, eps] = stats.skew(df_sample.iloc[db.core_sample_indices_][(eps, min_samples)].value_counts())
        
        geodesic_score = silhouette_score(np.array(df_sample[['lat', 'lng']].iloc[db.core_sample_indices_]).tolist(), 
                          db.labels_[db.core_sample_indices_], metric="haversine", #sample_size=3000
                         )
        
        df_db_silhouette.loc[min_samples, eps] = geodesic_score

In [36]:
df_db_cluster_size

0.005 0.006 0.007 0.008 0.010
5    301   140    60    36    14
8    220   167   102    43    17
10   150   158    99    56    18
15    42    73    84    79    26
20    20    30    41    54    44

Based on the results from grid search, I selected 20 as my minimum sample size and 0.008 as my epsilon because it produced the highest silhouette score  

In [38]:
df_db_silhouette

0.005     0.006     0.007     0.008     0.010
5  -0.022912 -0.339643 -0.575331 -0.486664 -0.472554
8   0.130922  -0.06417 -0.244677 -0.478547 -0.450932
10  0.159936  0.109178 -0.077503 -0.329836 -0.435346
15  0.010022  0.095429  0.158244  0.042078 -0.428831
20  0.132259  0.130898  0.188522   0.19855 -0.042327

In [39]:
fig = go.Figure()
for eps in [.005, .006, .007, .008, .01]:
    kn = KneeLocator(df_db_silhouette.index, y=df_db_silhouette[eps], curve='concave', direction='increasing')
    print('epsilon:', eps, 'min samples knee:', kn.knee)
    fig.add_trace(go.Scatter(x=df_db_silhouette.index, y=df_db_silhouette[eps], mode='lines+markers', name=eps))
fig.update_layout(plot_bgcolor='rgba(0, 0, 0, 0)',
                  title='Silhouette score',
                  xaxis=dict(title='Min samples'),
                  yaxis=dict(title='silhouette score'),
                  height=400, width=600
                 )
fig.show()

fig = go.Figure()
for min_samples in [5, 8, 10, 15, 20]:
    kn = KneeLocator(df_db_silhouette.columns, y=df_db_silhouette.transpose()[min_samples], curve='convex', direction='decreasing')
    print('min samples:', min_samples, 'epsilon knee:', kn.knee)
    
    fig.add_trace(go.Scatter(x=df_db_silhouette.columns, y=df_db_silhouette.transpose()[min_samples], mode='lines+markers', name=min_samples))
fig.update_layout(plot_bgcolor='rgba(0, 0, 0, 0)',
                  title='Standard deviation of cluster sizes',
                  xaxis=dict(title='epsilon'),
                  yaxis=dict(title='silhouette score'),
                  height=400, width=600
                 )
fig.show()

epsilon: 0.005 min samples knee: 10
epsilon: 0.006 min samples knee: 10
epsilon: 0.007 min samples knee: 10
epsilon: 0.008 min samples knee: 5
epsilon: 0.01 min samples knee: 5


min samples: 5 epsilon knee: 0.007
min samples: 8 epsilon knee: 0.008
min samples: 10 epsilon knee: 0.005
min samples: 15 epsilon knee: 0.005
min samples: 20 epsilon knee: 0.005


In [40]:
db = DBSCAN(eps=0.008, min_samples=20, metric='haversine', n_jobs=-1).fit(df_sample_lat_lng)
df_sample['cluster_id_db'] = db.labels_
df_sample['cluster_color'] = df_sample['cluster_id_db'].apply(lambda x: colors[x])

In [41]:
fig = go.Figure()
# for cl in sorted(df_sample['cluster_id_db'].unique(), reverse=True):
fig.add_trace(go.Scattermapbox( lat=df_sample['lat'],  
                                lon=df_sample['lng'], 
                                mode='markers',
                                marker=go.scattermapbox.Marker(size=5, 
                                                              opacity=1, 
                                                              color=df_sample['cluster_color'], 
                                                              colorbar=dict(title='cluster'))
                              ))
# update mapbox style and layout
fig.update_mapboxes(
    domain=dict(column=2),
    style='mapbox://styles/mapbox/light-v10',
    zoom=8,
    center=map_centre
)

fig.update_layout(title='DBSCAN clustering (min samples: 20, epsilon: 0.008)', height=600, margin_t=50, showlegend=False, mapbox_accesstoken=mapboxtoken
                 )

fig.show()

# Spatial association between pokemon species
In this section I will use the Jaccard similarity coefficients (a measure of similarity between sets) to identify pokemon species that spawned near each other. It is formally defined as the size of intersection divided by the size of union of two sets. In the context of pokemon spawns, the coefficient between two pokemon species can be calculated by counting the number of clusters they both appeared in, divided by the number of clusters either/both of them appeared in. The coefficient equals 1 if the two species always appeared in the same clusters. 

In [42]:
# exclude outliers from the DBSCAN clustering
df_sample_clustered = df_sample[df_sample['cluster_id_db']!=-1]#.iloc[db.core_sample_indices_].copy(deep=True)

In [43]:
# aggregate pokemons spawns to the cluster level
df_db_clusters = df_sample_clustered.groupby('cluster_id_db').agg({'num':'count'}).reset_index()
pokemon_dummy_cols = [col_name for col_name in df_sample_clustered.columns.tolist() if ('pkm' in col_name)]
print(len(pokemon_dummy_cols))
df_db_cluster_pokemons = df_sample_clustered.groupby('cluster_id_db').agg({pkm:'sum' for pkm in pokemon_dummy_cols}).reset_index()
df_db_clusters = df_db_clusters.merge(df_db_cluster_pokemons, on='cluster_id_db')

137


In [44]:
# compute pair-wise jaccard similarity coefficients

jaccard_coef_dict = {}

for i, pkm1 in enumerate(pokemon_dummy_cols):
    jc_pkm1_dict = {}
    pkm1_clusters = df_sample_clustered[df_sample_clustered[pkm1]>0]['cluster_id_db'].unique()
    for pkm2 in pokemon_dummy_cols[i:]:
        if (df_sample_clustered[pkm1].sum() > 0) & (df_sample_clustered[pkm2].sum() > 0) & (pkm1 != pkm2):
            pkm2_clusters = df_sample_clustered[df_sample_clustered[pkm2]>0]['cluster_id_db'].unique()
            intersect = set(pkm2_clusters).intersection(set(pkm1_clusters))
            union = set(pkm2_clusters).union(set(pkm1_clusters))
            jaccard_coef = len(intersect)/len(union)
            jc_pkm1_dict[pkm2] = (jaccard_coef, pkm1, len(intersect))
            
    
    jaccard_coef_dict[pkm1] = jc_pkm1_dict
    
df_jc = pd.DataFrame(jaccard_coef_dict)

In [45]:
#Inspect the top scoring pairs of pokemons
pd.concat([df_jc[pkm] for pkm in df_jc.index if (df_sample_clustered[df_sample_clustered[pkm]>0]['cluster_id_db'].nunique()<10000)
                                               &(df_sample_clustered[df_sample_clustered[pkm]>0]['cluster_id_db'].nunique()>5)]).reset_index().sort_values(0, ascending=False).head(10)

index                                      0
3269      pkm_Zubat   (0.8867924528301887, pkm_Pidgey, 47)
4468      pkm_Zubat  (0.8823529411764706, pkm_Spearow, 45)
3240    pkm_Rattata   (0.8627450980392157, pkm_Pidgey, 44)
4032      pkm_Zubat  (0.8269230769230769, pkm_Rattata, 43)
3253    pkm_Spearow   (0.8113207547169812, pkm_Pidgey, 43)
4016    pkm_Spearow                (0.75, pkm_Rattata, 39)
3035    pkm_Spearow     (0.723404255319149, pkm_Paras, 34)
855     pkm_Spearow     (0.723404255319149, pkm_Eevee, 34)
905   pkm_Growlithe    (0.7058823529411765, pkm_Ekans, 24)
3051      pkm_Zubat                   (0.7, pkm_Paras, 35)

In [46]:
df_jc.sort_values('pkm_Goldeen', ascending=False)['pkm_Goldeen'].head(5)

pkm_Horsea         (0.6363636363636364, pkm_Goldeen, 7)
pkm_Jigglypuff     (0.5384615384615384, pkm_Goldeen, 7)
pkm_Tauros         (0.4166666666666667, pkm_Goldeen, 5)
pkm_Pinsir         (0.4166666666666667, pkm_Goldeen, 5)
pkm_Sandshrew     (0.35714285714285715, pkm_Goldeen, 5)
Name: pkm_Goldeen, dtype: object

In [47]:
df_jc.sort_values('pkm_Growlithe', ascending=False)['pkm_Growlithe'].head(5)

pkm_Rattata    (0.6086956521739131, pkm_Growlithe, 28)
pkm_Meowth     (0.6060606060606061, pkm_Growlithe, 20)
pkm_Zubat                    (0.58, pkm_Growlithe, 29)
pkm_Paras      (0.5609756097560976, pkm_Growlithe, 23)
pkm_Pidgey     (0.5490196078431373, pkm_Growlithe, 28)
Name: pkm_Growlithe, dtype: object

The pokemons species pairs that have the highest Jaccard index are Rattata and Pidgey, two of the most commonly seen pokemons. In terms of of less common pokemons, some interesting pairs are: 
* Horsea and Goldeen, both water types, Jaccard similarity: 64%
* Growlithe and Meowth, both feline, Jaccard similarity: 61% 


In [48]:
import folium.plugins

m = folium.plugins.DualMap(location=[37.6965,-122.1158], tiles="Cartodb Positron", zoom_start=9)

for i in range(len(df_plot_sample_pkm_dict['goldeen'])-1):#stations['features']:
    lon, lat = df_plot_sample_pkm_dict['goldeen'].iloc[i]['lng'], df_plot_sample_pkm_dict['goldeen'].iloc[i]['lat']
    icon_path = '../static/img/pkm-goldeen.png'
    icon = folium.features.CustomIcon(icon_path,
                                      icon_size=(20, 20))
    marker = folium.map.Marker([lat, lon], icon=icon,
                              )
    m.m1.add_child(marker)
    
for i in range(len(df_plot_sample_pkm_dict['horsea'])-1):#stations['features']:
    lon, lat = df_plot_sample_pkm_dict['horsea'].iloc[i]['lng'], df_plot_sample_pkm_dict['horsea'].iloc[i]['lat']
    icon_path = '../static/img/pkm-horsea.png'
    icon = folium.features.CustomIcon(icon_path,
                                      icon_size=(20, 20))
    
    marker = folium.map.Marker([lat, lon], icon=icon,
                              )
    m.m1.add_child(marker)
    
for i in range(len(df_plot_sample_pkm_dict['meowth'])-1):#stations['features']:
    lon, lat = df_plot_sample_pkm_dict['meowth'].iloc[i]['lng'], df_plot_sample_pkm_dict['meowth'].iloc[i]['lat']
    icon_path = '../static/img/pkm-meowth.png'
    icon = folium.features.CustomIcon(icon_path,
                                      icon_size=(20, 20))
    marker = folium.map.Marker([lat, lon], icon=icon,
                              )
    m.m2.add_child(marker)
    
for i in range(len(df_plot_sample_pkm_dict['growlithe'])-1):#stations['features']:
    lon, lat = df_plot_sample_pkm_dict['growlithe'].iloc[i]['lng'], df_plot_sample_pkm_dict['growlithe'].iloc[i]['lat']
    icon_path = '../static/img/pkm-growlithe.png'
    icon = folium.features.CustomIcon(icon_path,
                                      icon_size=(20, 20))
    
    marker = folium.map.Marker([lat, lon], icon=icon,
                              )
    m.m2.add_child(marker)
    

In [ ]:
m

In [ ]:
# FOR LEARNING, NOT SUITABLE FOR LARGE NUMBER OF CLUSTERS

# As a learning exercise, I will implement K-Means clustering from scratch. 
# def k_means_from_scratch(data, k):
#     random.seed(0)
#     centroids = random.sample(data,k)
#     counter = 0
#     while counter < 1000:
#         clustering = {cluster:np.empty(shape=(0,2)) for cluster in np.arange(k)}
#         # for each data point
#         for i, spwn in enumerate(data):
#             # calculate distance from each centroid
#             distances = [((spwn[0]-c[0])**2+(spwn[1]-c[1])**2)**.5 for c in centroids]
#             # add data point to the cluster of the centroid that it is closest to
#             clustering[np.argmin(distances)] = np.vstack([clustering[np.argmin(distances)],spwn])

#         # calculate new centroids as the mid point of each cluster 
#         new_centroids = np.array([clustering[c].mean(axis=0) for c in np.arange(k)])

#         # update centroids until there are no longer changing
#         if np.array_equiv(new_centroids,centroids):
#             print(f'Converged, final centroids: {centroids}')
#             break

#         centroids = new_centroids
#         counter += 1
        
#         clustering_dict = {key:{'centroid':centroids[key], 
#                                 'size':len(clustering[key]),
#                                 'points':clustering[key]} for key, values in clustering.items()}

#     return clustering_dict

### Agglomerative clustering
An alternative clustering method is Agglomerative Clustering. It is a hierarchical clustering starting with each data point being in its own cluster. Clusters that are closest to each other are paired up in each iteration until the desired number of clusters is reached or until the distance threshold is met. 

In [ ]:
# from sklearn.cluster import AgglomerativeClustering
df_lat_lng = np.array(df[['lat', 'lng']].head(10000)).tolist()
aggclustering = AgglomerativeClustering(n_clusters=10, #distance_threshold=0.0001, 
                                        compute_distances=True).fit(df_lat_lng)